In [221]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler , LabelEncoder
from sklearn.ensemble import ExtraTreesClassifier
from imblearn.over_sampling import RandomOverSampler 

In [222]:
# Proses melakukan import dataset yang diperlukan
test_set = pd.read_csv('dataset/test_feature.csv')
features = pd.read_csv('dataset/train_features.csv')
labels = pd.read_csv('dataset/train_label.csv')

In [223]:
# Menampilkan jumlah missing value pada features
na_feature = features.isna().sum()
na_feature

facilities    301
rating        637
location        0
dtype: int64

In [224]:
# Proses mengisi missing values string pada features dengan 'NULL'
features = features.fillna('NULL')

In [225]:
features['rating_average'] = 0
features['review_count'] = 0

for ind in features.index:
    if (features['rating'][ind] != "NULL"):
        l = []
        for t in features['rating'][ind].split():
            try:
                l.append(float(t))
            except ValueError:
                pass
        if (len(l) == 2):
            features['rating_average'][ind] = l[0]
            features['review_count'][ind] = l[1]
            
        else:
            features['rating'][ind] = "NULL"
    else:
        features['rating'][ind] = "NULL"


C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\1138038384.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['rating_average'][ind] = l[0]
C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\1138038384.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['review_count'][ind] = l[1]
C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\1138038384.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['review_coun

In [226]:
features['review_multiple'] = 0
for ind in features.index:
    features['review_multiple'][ind] = features['rating_average'][ind] * features['review_count'][ind] / features['review_count'].sum()

C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\46165240.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['review_multiple'][ind] = features['rating_average'][ind] * features['review_count'][ind] / features['review_count'].sum()


In [227]:
features['Restaurant']=0
features['Bar']=0
features["Gym"]=0
features['Internet']=0
features['Swimming Pools']=0
features['n_features'] = 0



for ind in features.index:
    features['facilities'][ind] = features['facilities'][ind].lower()
    
    n_features = 0

    if (features['rating'][ind] != "NULL"):

        if 'restaurant' in features['facilities'][ind] :
            features['Restaurant'][ind] = int(1)
            n_features += 1

        if 'bar' in features['facilities'][ind] :
            features['Bar'][ind] = int(1)
            n_features += 1

        if 'swimmingpools' in features['facilities'][ind] :
            features['Swimming Pools'][ind] = int(1)
            n_features += 1 

        if 'gym' in features['facilities'][ind] :
            features['Gym'][ind] = int(1)
            n_features += 1

        if 'internet' in features['facilities'][ind]  :
            features['Internet'][ind] = int(1)
            n_features += 1

        if 'intrnet' in features['facilities'][ind]  :
            features['Internet'][ind] = int(1)
            n_features += 1
        
        features['n_features'][ind] = n_features

       


C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\420034004.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['facilities'][ind] = features['facilities'][ind].lower()
C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\420034004.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  features['Restaurant'][ind] = int(1)
C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\420034004.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

In [228]:
features = features.drop(columns='location')

## BATAS PENGECEKAN DATAFRAME

In [229]:
features["review_multiple"].describe()

count    3066.000000
mean        0.002401
std         0.005502
min         0.000000
25%         0.000157
50%         0.000829
75%         0.002434
max         0.061020
Name: review_multiple, dtype: float64

In [230]:
features.iloc[312]

facilities                    restaurantbargym
rating             7.1 Very GoodFrom 8 reviews
rating_average                             7.1
review_count                                 8
review_multiple                       0.001266
Restaurant                                   1
Bar                                          1
Gym                                          1
Internet                                     0
Swimming Pools                               0
n_features                                   3
Name: 312, dtype: object

In [231]:
for ind in labels.index:
    string = labels['Price'][ind]
    string = string.replace( 'avg/night', '')
    string = string.replace( ',', '')
    labels['Price'][ind] = float(string)
labels.head()

Price
0  13500.0
1  13000.0
2  19000.0
3   6000.0
4  20000.0

In [232]:
# Drop Outlier
labels = labels.drop(index= [697,828,1030,1424,1856,2346])
features = features.drop(index= [697,828,1030,1424,1856,2346])

In [233]:
labels = labels.astype("int32")

In [234]:
features = features.drop(columns = ['facilities','rating'])

In [235]:
x_train, x_test, y_train, y_test = train_test_split(features,labels, test_size = 0.3, random_state = 23)

In [236]:
from sklearn.ensemble import RandomForestRegressor


# Initializing
model = RandomForestRegressor(verbose=2, n_estimators= 200, criterion='absolute_error', random_state= 23, bootstrap=False, n_jobs=-1)

# Training
model.fit(x_train,y_train)

C:\Users\kofif\AppData\Local\Temp\ipykernel_22036\3345646010.py:8: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  model.fit(x_train,y_train)
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 16 concurrent workers.


building tree 1 of 200building tree 2 of 200

building tree 3 of 200
building tree 4 of 200
building tree 5 of 200
building tree 6 of 200
building tree 7 of 200
building tree 8 of 200
building tree 9 of 200
building tree 10 of 200
building tree 11 of 200
building tree 12 of 200
building tree 13 of 200
building tree 14 of 200
building tree 15 of 200
building tree 16 of 200
building tree 17 of 200
building tree 18 of 200
building tree 19 of 200
building tree 20 of 200
building tree 21 of 200
building tree 22 of 200
building tree 23 of 200
building tree 24 of 200
building tree 25 of 200
building tree 26 of 200
building tree 27 of 200
building tree 28 of 200
building tree 29 of 200
building tree 30 of 200
building tree 31 of 200
building tree 32 of 200


[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:    0.3s


building tree 33 of 200
building tree 34 of 200
building tree 35 of 200
building tree 36 of 200
building tree 37 of 200
building tree 38 of 200
building tree 39 of 200
building tree 40 of 200
building tree 41 of 200
building tree 42 of 200
building tree 43 of 200
building tree 44 of 200
building tree 45 of 200
building tree 46 of 200
building tree 47 of 200
building tree 48 of 200
building tree 49 of 200
building tree 50 of 200
building tree 51 of 200
building tree 52 of 200
building tree 53 of 200
building tree 54 of 200
building tree 55 of 200
building tree 56 of 200
building tree 57 of 200
building tree 58 of 200
building tree 59 of 200
building tree 60 of 200
building tree 61 of 200
building tree 62 of 200
building tree 63 of 200
building tree 64 of 200
building tree 65 of 200
building tree 66 of 200
building tree 67 of 200
building tree 68 of 200
building tree 69 of 200
building tree 70 of 200
building tree 71 of 200
building tree 72 of 200
building tree 73 of 200
building tree 74

[Parallel(n_jobs=-1)]: Done 130 tasks      | elapsed:    1.9s


building tree 149 of 200
building tree 150 of 200
building tree 151 of 200
building tree 152 of 200
building tree 153 of 200
building tree 154 of 200
building tree 155 of 200
building tree 156 of 200
building tree 157 of 200
building tree 158 of 200
building tree 159 of 200
building tree 160 of 200
building tree 161 of 200
building tree 162 of 200
building tree 163 of 200
building tree 164 of 200
building tree 165 of 200
building tree 166 of 200
building tree 167 of 200
building tree 168 of 200
building tree 169 of 200
building tree 170 of 200
building tree 171 of 200
building tree 172 of 200
building tree 173 of 200
building tree 174 of 200
building tree 175 of 200
building tree 176 of 200
building tree 177 of 200
building tree 178 of 200
building tree 179 of 200
building tree 180 of 200
building tree 181 of 200
building tree 182 of 200
building tree 183 of 200
building tree 184 of 200
building tree 185 of 200
building tree 186 of 200
building tree 187 of 200
building tree 188 of 200


[Parallel(n_jobs=-1)]: Done 200 out of 200 | elapsed:    2.8s finished


RandomForestRegressor(bootstrap=False, criterion='absolute_error',
                      n_estimators=200, n_jobs=-1, random_state=23, verbose=2)

In [237]:
y_pred = model.predict(x_test)

[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done 130 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done 200 out of 200 | elapsed:    0.0s finished


In [238]:
from sklearn.metrics import mean_absolute_error

mean_absolute_error(y_pred, y_test)


2833.046296296296

<h1> Prediksi yang test_feature <h1>

In [239]:
test_set.head()

ID                             facilities                        rating   
0   0  GymrestaurantbarInternetSwimmingPools   8.0 ExcellentFrom 1 reviews  \
1   1           Poolrestaurantgyminternetbar  7.4 Very GoodFrom 22 reviews   
2   2            BARSwimmingPoolsInternetgym        0.0 FairFrom 4 reviews   
3   3   gymSwimmingPoolsBARintrnetRestaurant  6.8 Very GoodFrom 13 reviews   
4   4            gymRestaurantpoolbarintrnet        0.0 FairFrom 9 reviews   

    location  
0     Stokol  
1  Hallerson  
2  Hallerson  
3    Andeman  
4  Hallerson

In [ ]:
import numpy as np
test_set['rating_average'] = np.NaN
test_set['review_count'] = np.NaN
test_set['review_multiple'] = np.NaN
for ind in test_set.index:
    if (test_set['rating'][ind] != "NULL"):
        l = []
        for t in test_set['rating'][ind].split():
            try:
                l.append(float(t))
            except ValueError:
                pass
        if (len(l) == 2):
            test_set['rating_average'][ind] = l[0]
            test_set['review_count'][ind] = l[1]
            test_set['review_multiple'][ind] = l[0]*l[1]
        else:
            test_set['rating'][ind] = "NULL"
    else:
        test_set['rating'][ind] = "NULL"


print(test_set)

In [ ]:
test_set['Restaurant']=''
test_set['Bar']=''
test_set["Gym"]=''
test_set['Internet']=''
test_set['Swimming Pools']=''


In [ ]:
test_set.head()

In [ ]:
for ind in test_set.index:
    test_set['facilities'][ind] = test_set['facilities'][ind].lower()

    if 'restaurant' in test_set['facilities'][ind] :
        test_set['Restaurant'][ind] = 1
    else :
        test_set['Restaurant'][ind] = 0

    if 'bar' in test_set['facilities'][ind] :
        test_set['Bar'][ind] = 1
    else :
        test_set['Bar'][ind] = 0

    if 'swimmingpools' in test_set['facilities'][ind] :
        test_set['Swimming Pools'][ind] = 1
    else :
        test_set['Swimming Pools'][ind] = 0    

    if 'gym' in test_set['facilities'][ind] :
        test_set['Gym'][ind] = 1
    else :
        test_set['Gym'][ind] = 0   

    if 'internet' or 'intrnet' in test_set['facilities'][ind]  :
        test_set['Internet'][ind] = 1
    else :
        test_set['Internet'][ind] = 0



In [ ]:
test_set = pd.get_dummies(test_set, columns = ['location'], dtype= int)

In [ ]:
test_set = test_set.drop(columns = ['facilities','rating','ID'])

In [ ]:
test_set.head()

In [ ]:
result = model.predict(test_set)

In [ ]:
# Proses penyesuaian hasil prediksi dengan format submisi

# Proses pengubahan array menjadi dataframe
df = pd.DataFrame(result, columns=["Price"])

# Proses pengambilan respondent id original
test_set = pd.read_csv('dataset/test_feature.csv')
test_set.loc[:,"ID"]

# Proses pembuatan dataframe akhir 
df_final = test_set.ID
df_final =  pd.DataFrame(df_final, columns=["ID"])
df_final["Price"]= df["Price"] 

# Proses export dataframe menjadi csv
df_final.to_csv("prediction/bismillah_1.csv", index=False) 